# Synteza Tacotron2

**Właściciel tego notatnika: Tadejro**

Połączenie wszystkiego, co do tej pory powstało na Mekatronie. Podziękowania dla:
- Meka
- Adam is cool and stuff – za orginalną wersję tacotronową
- Heroba – za zrobienie wersji z formularzami (Link: https://colab.research.google.com/drive/1FXQRoCRl4NW1DY77HiRcIySjrjS-wfSb)
- Patryka – za funkcję "zagraniczny_głos" i naprawienie pobierania z dysków Google
- Vojaka – za oryginalną wersję tego notatnika

Obecnie notatnik posiada drobny błąd – przy pierwszej syntezie po uruchomieniu tego Colaba skrypt "zagraniczny_głos" nie załapuje, więc trzeba jeszcze raz wygenerować. Wszystkie kolejne generacje są już OK. Jak ktoś zna się na programowaniu, to może pomóc mi w naprawie tego błędu.

----------------------------------------------------------------

# Krok 1: Sprawdzenie karty graficznej

In [ ]:
!nvidia-smi -L
!python3 -V

GPU 0: Tesla T4 (UUID: GPU-2f382b71-7fb8-a963-af87-36a3d0214937)
Python 3.8.10


----------------------------------------------------------------

# Krok 2: Pobranie wymagań syntezy, ukryty by nie zapychał miejsca.


In [ ]:
#@title
#Instalacja Tacotrona i Waveglow
!pip install --upgrade --no-cache-dir gdown
!pip install pydub
import locale
from pydub import AudioSegment


def getpreferredencoding(do_setlocale = True):
    return "UTF-8"
locale.getpreferredencoding = getpreferredencoding


%tensorflow_version 2.x
import os
from os.path import exists, join, basename, splitext
!pip install gdown
# Repozytorium zawierające poprawkę pozwalającą uzywać na colabie tensorflow 2.x
git_repo_url = 'https://github.com/8tm/mekatron2.git'
project_name = splitext(basename(git_repo_url))[0]
if not exists(project_name):
  # clone and install
  !git clone -q --recursive {git_repo_url}
  !cd {project_name}/waveglow && git checkout 2fd4e63
  !pip install -q librosa unidecode

!pip install ffmpeg
import sys
sys.path.append(join(project_name, 'waveglow/'))
sys.path.append(project_name)
import time
import matplotlib
import matplotlib.pylab as plt
import gdown
d = 'https://drive.google.com/uc?id='

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Attempting uninstall: gdown
    Found existing installation: gdown 4.4.0
    Uninstalling gdown-4.4.0:
      Successfully uninstalled gdown-4.4.0
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Colab only includes TensorFlow 2.x; %tensorflow_version has no effect.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
error: pathspec '2fd4e63' did not match any file(s) known to git
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.9/235.9 KB 18.2 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
  Created wheel for ffmpeg: filename=ffmpeg-1.4-py3-none-any.whl size=6084 sha256=60b3f480285306f2607b29af3561db6988c19ab3321e0064d1ee19544e66d283
  Stored in directory: /root/.cache/pip/wheels/30/3

----------------------------------------------------------------

# Krok 3: Ustawienie modelu

In [ ]:

#@title
#@markdown Jeżeli będzie problem z uprawnieniami do pliku, a są ustawione jak należy, to trzeba trochę poczekać bądź sprawdzić nazwę.
#@markdown ### Wymuszone pobieranie modeli
#@markdown Po prostu ponownie pobierze zaznaczone modele nawet, jeśli wcześniej były pobrane.
pobierz_model_tacotron2 = True #@param{type:'boolean'}
pobierz_model_waveglow = True #@param{type:'boolean'}

#@markdown ### ID modeli (pobiera je się z linku)
#@markdown ID modelu tacotron2:
tacotron2_link = "1df5KQ0WwxllwLsEbp7vdzuqHshhuM5JU" #@param{type:"string"}
#@markdown ID modelu waveglow:
waveglow_link = "17xuBnKr6gtGfR21Hmsgx_rk8kKPrEWrn" #@param{type:"string"}
tacotron2_pretrained_model = 'tacotron2'
if not exists(tacotron2_pretrained_model) or pobierz_model_tacotron2:
    print("Pobieranie modelu Tacotron2")
    gdown.download(d+tacotron2_link.strip(), tacotron2_pretrained_model, quiet=False)
    print("Model Tacotron2 pobrany pomyślnie")

waveglow_pretrained_model = 'waveglow'
if not exists(waveglow_pretrained_model) or pobierz_model_waveglow:
    print("Pobieranie modelu Waveglow")
    gdown.download(d+waveglow_link.strip(), waveglow_pretrained_model, quiet=False)
    print("Model Waveglow pobrany pomyślnie")

#@markdown

Pobieranie modelu Tacotron2


Downloading...
From: https://drive.google.com/uc?id=1df5KQ0WwxllwLsEbp7vdzuqHshhuM5JU
To: /content/tacotron2
100%|██████████| 338M/338M [00:07<00:00, 43.0MB/s]


Model Tacotron2 pobrany pomyślnie
Pobieranie modelu Waveglow


Downloading...
From: https://drive.google.com/uc?id=17xuBnKr6gtGfR21Hmsgx_rk8kKPrEWrn
To: /content/waveglow
100%|██████████| 1.38G/1.38G [00:21<00:00, 64.8MB/s]

Model Waveglow pobrany pomyślnie


# Krok 4: Kod syntezy, ukryty by nie zapychał miejsca

In [ ]:
#@title
#Wstępne przygotowania Tacotrona i Waveglow
%matplotlib inline
import IPython.display as ipd
import numpy as np
import torch

from hparams import create_hparams
from model import Tacotron2
from layers import TacotronSTFT
from audio_processing import griffin_lim
from text import text_to_sequence
from denoiser import Denoiser

graph_width = 900
graph_height = 360
def plot_data(data, figsize=(int(graph_width/100), int(graph_height/100))):
    %matplotlib inline
    fig, axes = plt.subplots(1, len(data), figsize=figsize)
    for i in range(len(data)):
        axes[i].imshow(data[i], aspect='auto', origin='bottom',
                       interpolation='none', cmap='inferno')
    fig.canvas.draw()
    plt.show()

!gdown --id '1uciIczSNxzjhWZEzJ_gB2pzLGrtXSQHc'
thisdict = {}
for line in reversed((open('merged.dict.txt', "r").read()).splitlines()):
    thisdict[(line.split(" ",1))[0]] = (line.split(" ",1))[1].strip()
def ARPA(text):
    out = ''
    for word_ in text.split(" "):
        word=word_; end_chars = ''
        while any(elem in word for elem in r"!?,.;") and len(word) > 1:
            if word[-1] == '!': end_chars = '!' + end_chars; word = word[:-1]
            if word[-1] == '?': end_chars = '?' + end_chars; word = word[:-1]
            if word[-1] == ',': end_chars = ',' + end_chars; word = word[:-1]
            if word[-1] == '.': end_chars = '.' + end_chars; word = word[:-1]
            if word[-1] == ';': end_chars = ';' + end_chars; word = word[:-1]
            else: break
        try: word_arpa = thisdict[word.upper()]
        except: word_arpa = ''
        if len(word_arpa)!=0: word = "{" + str(word_arpa) + "}"
        out = (out + " " + word + end_chars).strip()
    if out[-1] != ";": out = out + ";"
    return out

#torch.set_grad_enabled(False)

# initialize Tacotron2 with the pretrained model
hparams = create_hparams()

import os
from os.path import exists, join, basename, splitext
!pip install gdown
git_repo_url = 'https://github.com/jik876/hifi-gan.git'
project_name = splitext(basename(git_repo_url))[0]
if not exists(project_name):
  # clone and install
  !git clone -q --recursive {git_repo_url}
  !cd {project_name}/waveglow && git checkout 2fd4e63
  !pip install -q librosa unidecode

!pip install gdown
import gdown
d = 'https://drive.google.com/uc?id='
gdown.download(d+r'1qpgI41wNXFcH-iKq1Y42JlBC9j0je8PW', 'pretrained', quiet=False); print("Model Downloaded")
gdown.download(d+r'1pAB2kQunkDuv6W5fcJiQ0CY8xcJKB22e', 'config.json', quiet=False); print("Config Downloaded")
try:
    os.mkdir("test_files")
except FileExistsError:
    pass

/content/mekatron2/text/__init__.py:74: SyntaxWarning: "is not" with a literal. Did you mean "!="?
  return s in _symbol_to_id and s is not '_' and s is not '~'
/content/mekatron2/text/__init__.py:74: SyntaxWarning: "is not" with a literal. Did you mean "!="?
  return s in _symbol_to_id and s is not '_' and s is not '~'


/usr/local/lib/python3.8/dist-packages/gdown/cli.py:121: FutureWarning: Option `--id` was deprecated in version 4.3.1 and will be removed in 5.0. You don't need to pass it anymore to use a file ID.
  warnings.warn(
Downloading...
From: https://drive.google.com/uc?id=1uciIczSNxzjhWZEzJ_gB2pzLGrtXSQHc
To: /content/merged.dict.txt
100% 7.94M/7.94M [00:00<00:00, 117MB/s]
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
/bin/bash: line 0: cd: hifi-gan/waveglow: No such file or directory
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


Downloading...
From: https://drive.google.com/uc?id=1qpgI41wNXFcH-iKq1Y42JlBC9j0je8PW
To: /content/pretrained
100%|██████████| 55.8M/55.8M [00:00<00:00, 164MB/s]


Model Downloaded


Downloading...
From: https://drive.google.com/uc?id=1pAB2kQunkDuv6W5fcJiQ0CY8xcJKB22e
To: /content/config.json
100%|██████████| 799/799 [00:00<00:00, 2.16MB/s]

Config Downloaded


----------------------------------------------------------------

# Krok 5: Ustawienie parametrów syntezy



In [ ]:
#@title
#@markdown **Częstotliwość próbkowania**. Większa częstotliwość próbkowania zwiększa prędkość głosu i jego ton. (domyślnie jest 22050). Lepiej nie zmieniać bazowej wartości.
hparams.sampling_rate = 22050 #@param{type:'number', min:'0', max:'384000'}
#@markdown **Maksymalna ilość iteracji dekodera** wpływa na długość wygenerowanego głosu.

#@markdown Można zwiększyć, by syntezator mógł wygenerować dłuższy głos (domyślnie 1000)
hparams.max_decoder_steps = 5000# @param{type:'number',min:1}
hparams.gate_threshold = 0.1 # Model must be 90% sure the clip is over before ending generation (the higher this number is, the more likely that the AI will keep generating until it reaches the Max Decoder Steps)
model = Tacotron2(hparams)
model.load_state_dict(torch.load(tacotron2_pretrained_model)['state_dict'])
_ = model.cuda().eval().half()

# Załaduj Waveglow
waveglow = torch.load(waveglow_pretrained_model)['model']
waveglow.cuda().eval().half()
for k in waveglow.convinv:
    k.float()
denoiser = Denoiser(waveglow)

----------------------------------------------------------------

# Krok 6: Synteza

Od teraz dla zaoszczędzenia miejsca przykładowe teksty można wybrać z wysuwanego menu w inpucie *text*.

In [ ]:
#@title
#@markdown **Tekst do odczytania**
text = "Powierzy\u0142em swoje dziadki dla Antosi i jej Matki. Dzi\u015B Antosia powidzia\u0142a, \u017Ce \u017Cadnego dzieciaka nie bra\u0142a wi\u0119c i nie od da\u0142a. Co za wredna pa\u0142a." #@param ["Nam strzelać nie kazano. Wstąpiłem na działo. I spojrzałem na pole. dwieście armat grzmiało. Artyleryji ruskiej ciągną się szeregi. Prosto, długo, daleko, jako morza brzegi.", "Wasali przytłoczyło bogactwo i ogrom lądu i nie byli w stanie znaleźć miejsca na wybudowanie ich nowej stolicy.", "Korzystanie z dwóch broni oznacza, że nie masz żadnej ochrony i nie możesz blokować. Ale jeśli uderzysz dwiema broniami naraz, wróg może już nie mieć szansy odpowiedzieć.", "Z gwiazd obłąkanych, z włosów czesanych, iskry padają, jak z polskiej szabli. widzą je diabli, odpowiadają błyskami. Lecą. świst piór buki ugina.", "Jesteś dla mnie jak starszy brat. Nigdy nie miałem starszego brata, ani nawet młodszego. Moi rodzice mnie nie kochali, ale to musiało być dla nich bardzo trudne.", "Wiesz... Zabawne jest to, że często jest tak, że najbardziej niebezpieczni okazują się właśnie ci, którzy działają dla wyższych celów.", "Niniejszym, w imieniu Aldmerskiego Dominium, na mocy konkordatu bieli i złota, aresztuję meka za wiarę w talosa.", "Przed użyciem zapoznaj się z treścią ulotki dołączonej do opakowania bądź skonsultuj się z lekarzem lub farmaceutą, gdyż każdy lek niewłaściwie stosowany zagraża Twojemu życiu lub zdrowiu.", "Elektrody otulone są metalowymi prętami otoczonymi sprasowaną otuliną. Dobierane są głównie w zależności od składu chemicznego, właściwości i gabarytów materiałów łączonych, ale także spodziewanej wytrzymałości złącza, rodzaju źródła prądu czy pozycji spawania."] {allow-input: true}

zagraniczny_głos = False#@param{type:"boolean"}
denoise_strength =  0.06#@param{type:"number"}
equalize = True #@param{type:"boolean"}
gan = True#@param{type:"boolean"}
_sigma = 1
speed_multiplier = 1
raw_input = False

import os
import glob

files = glob.glob('test_files/*')
for f in files:
    os.remove(f)

    if zagraniczny_głos:
      text = (text.replace("ch", "h"))
      text = (text.replace("Ch", "H"))
      text = (text.replace("ó", "u"))
      text = (text.replace("x", "ks"))
      text = (text.replace("v", "w"))
      text = (text.replace("rz", "ż"))
      text = (text.replace("Rz", "Ż"))
      text = (text.replace("ą ", "om "))
      text = (text.replace("ą, ", "om, "))
      text = (text.replace("ą. ", "om. "))
      text = (text.replace("ą? ", "om? "))
      text = (text.replace("ą! ", "om! "))
      text = (text.replace("ą.", "om."))
      text = (text.replace("ąb", "omb"))
      text = (text.replace("ąc", "onc"))
      text = (text.replace("ąć", "onć"))
      text = (text.replace("ąd", "ond"))
      text = (text.replace("ąf", "onf"))
      text = (text.replace("ąg", "ong"))
      text = (text.replace("ąh", "onh"))
      text = (text.replace("ąj", "onj"))
      text = (text.replace("ąk", "onk"))
      text = (text.replace("ąl", "oln"))
      text = (text.replace("ął", "oł"))
      text = (text.replace("ąm", "om"))
      text = (text.replace("ąn", "ołn"))
      text = (text.replace("ąp", "omp"))
      text = (text.replace("ąs", "ons"))
      text = (text.replace("ąś", "onś"))
      text = (text.replace("ąt", "ont"))
      text = (text.replace("ąw", "omw"))
      text = (text.replace("ąz", "onz"))
      text = (text.replace("ąż", "onż"))
      text = (text.replace("ąź", "onź"))
      text = (text.replace("ę ", "e "))
      text = (text.replace("ęb", "enb"))
      text = (text.replace("ęc", "enc"))
      text = (text.replace("ęć", "enć"))
      text = (text.replace("ęd", "end"))
      text = (text.replace("ęg", "eng"))
      text = (text.replace("ęk", "enk"))
      text = (text.replace("ęl", "el"))
      text = (text.replace("ęł", "eł"))
      text = (text.replace("ęn", "en"))
      text = (text.replace("ęp", "emp"))
      text = (text.replace("ęś", "enś"))
      text = (text.replace("ęs", "ens"))
      text = (text.replace("ęt", "ent"))
      text = (text.replace("ęw", "emw"))
      text = (text.replace("ęz", "enz"))
      text = (text.replace("ęż", "enż"))
      text = (text.replace("ęź", "enź"))
      text = (text.replace("ę. ", "e. "))
      text = (text.replace("ę.", "e."))
      text = (text.replace("ę, ", "e, "))
      text = (text.replace("ę? ", "e? "))
      text = (text.replace("ę! ", "e! "))

for i in text.split("\n"):
    if len(i) < 1:
        continue
    print(i)
    if raw_input:
        if i[-1] != ";":
            i=i+";"
    else:
        i = ARPA(i)
    print(i)

    sequence = np.array(text_to_sequence(text, ['basic_cleaners']))[None, :]
    sequence = torch.autograd.Variable(
    torch.from_numpy(sequence)).cuda().long()
    mel_outputs, mel_outputs_postnet, _, alignments = model.inference(sequence)
    with torch.no_grad():
      audio = waveglow.infer(mel_outputs_postnet, sigma=_sigma)
    audio_denoised = denoiser(audio, strength=denoise_strength)[:, 0]

    import scipy.io.wavfile
    from scipy.io.wavfile import write
    print("Zwykła wersja:")
    ipd.display(ipd.Audio(audio_denoised.cpu().numpy() , rate=hparams.sampling_rate * speed_multiplier))

    audio = ipd.Audio(audio_denoised.cpu().numpy(), rate=hparams.sampling_rate * speed_multiplier)
    audio = AudioSegment(audio.data[128:], frame_rate=hparams.sampling_rate * speed_multiplier, sample_width=2, channels=1)
    audio.export("test_files/testnt.wav", format="wav", bitrate="32k")

    !ffmpeg -loglevel quiet -i "test_files/testnt.wav" -ss 0.0000 -vcodec copy -acodec copy "test_files/test.wav"

    if equalize:
      !ffmpeg -loglevel quiet -y -i "test_files/test.wav" -ac 2 -af "aresample=44100:resampler=soxr:precision=15, equalizer=f=50:width_type=o:width=0.75:g=3.6, equalizer=f=3000:width_type=o:width=1.0:g=2.0, equalizer=f=10000:width_type=o:width=1.0:g=4.0" "test_EQ.wav"
      print("Wersja z EQ:")
      ipd.display(ipd.Audio("test_EQ.wav"))

    if gan:
      if equalize:
        print("")
        print("---------Logi generacji GAN---------")
        print("")
        !python hifi-gan/inference.py --checkpoint_file pretrained
        print("")
        print("---------Koniec logów generacji GAN---------")
        print("")
        print("Gan bez EQ:")
        ipd.display(ipd.Audio("generated_files/test_generated.wav"))
        !ffmpeg -loglevel quiet -y -i "generated_files/test_generated.wav" -ac 2 -af "aresample=44100:resampler=soxr:precision=15, equalizer=f=50:width_type=o:width=0.75:g=3.6, equalizer=f=3000:width_type=o:width=1.0:g=2.0, equalizer=f=10000:width_type=o:width=1.0:g=4.0" "generated_files/test_EQ.wav"
        print("Gan z EQ:")
        ipd.display(ipd.Audio("generated_files/test_EQ.wav"))
      else:
        print("")
        print("---------Logi generacji GAN---------")
        print("")
        !python hifi-gan/inference.py --checkpoint_file pretrained
        print("")
        print("---------Koniec logów generacji GAN---------")
        print("")
        print("Gan bez EQ:")
        ipd.display(ipd.Audio("generated_files/test_generated.wav"))
#@markdown

Powierzyłem swoje dziadki dla Antosi i jej Matki. Dziś Antosia powidziała, że żadnego dzieciaka nie brała więc i nie od dała. Co za wredna pała.
Powierzyłem swoje dziadki dla Antosi {AY1} jej Matki. Dziś Antosia powidziała, że żadnego dzieciaka {N AY1} brała więc {AY1} {N AY1} {AA1 D} dała. {K OW1} {Z AH0} wredna pała.;
Zwykła wersja:


Wersja z EQ:



---------Logi generacji GAN---------

Initializing Inference Process..
Loading 'pretrained'
Complete.
Removing weight norm...
/usr/local/lib/python3.8/dist-packages/torch/functional.py:632: UserWarning: stft will soon require the return_complex parameter be given for real inputs, and will further require that return_complex=True in a future PyTorch release. (Triggered internally at ../aten/src/ATen/native/SpectralOps.cpp:801.)
  return _VF.stft(input, n_fft, hop_length, win_length, window,  # type: ignore[attr-defined]
generated_files/test_generated.wav
generated_files/testnt_generated.wav

---------Koniec logów generacji GAN---------

Gan bez EQ:


Gan z EQ:


----------------------------------------------------------------